In [1]:
import json, folium
import pandas as pd
from postcodes_api import PostcodeApi

In [2]:
sch_stat = pd.read_excel('Datasets/scottish_schools_stats.xlsx')
sch_info = pd.read_excel('Datasets/scottish_schools_contact.xlsx', sheet_name='Open Schools')
dep = pd.read_excel('Datasets/postcode_deprivation.xlsx')

In [3]:
dep_rates = {}

for p,d in dep.values:
    dep_rates[p] = d

In [4]:
sch_stat.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2461 entries, 0 to 2460
Data columns (total 5 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Local Authority  2461 non-null   object
 1   SeedCode         2461 non-null   int64 
 2   School Name      2461 non-null   object
 3   School Type      2461 non-null   object
 4   Total pupils     2461 non-null   int64 
dtypes: int64(2), object(3)
memory usage: 96.3+ KB


In [5]:
sch_info.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2458 entries, 0 to 2457
Data columns (total 19 columns):
 #   Column                                   Non-Null Count  Dtype 
---  ------                                   --------------  ----- 
 0   Seed Code                                2458 non-null   int64 
 1   LA Name                                  2458 non-null   object
 2   Centre Type                              2458 non-null   object
 3   School Name                              2458 non-null   object
 4   Address Line1                            2458 non-null   object
 5   Address Line2                            2457 non-null   object
 6   Address Line3                            2458 non-null   object
 7   Post Code                                2458 non-null   object
 8   Unique Property Reference Number (UPRN)  2458 non-null   int64 
 9   Email                                    2458 non-null   object
 10  Phone Number                             2458 non-null   obj

In [6]:
sch_info = sch_info.rename(columns={'Seed Code' : 'SeedCode'})

In [7]:
sch_df = sch_info.merge(sch_stat, on='SeedCode', how='right')

In [8]:
sch_df.isna().sum()
sch_df.dropna(inplace=True)

In [9]:
sch_jsn = json.loads(sch_df.to_json(orient='records'))

In [10]:
postcodes = [sch['Post Code'] for sch in sch_jsn]

In [11]:
sch_loc_info = {'locs' : [], 'cities' : [], 'zones' : []}

for i in range(100,len(postcodes),100):

    sch_loc_info_100 = PostcodeApi().get_bulk_pos_info(postcodes[i-100:i])
    sch_loc_info['locs'] += sch_loc_info_100['locs']
    sch_loc_info['cities'] +=  sch_loc_info_100['cities']
    sch_loc_info['zones'] += sch_loc_info_100['zones']

    if (len(postcodes) - i) < 100:
        sch_loc_info_less = PostcodeApi().get_bulk_pos_info(postcodes[i:len(postcodes)])
        
        sch_loc_info['locs'] += sch_loc_info_less['locs']
        sch_loc_info['cities'] +=  sch_loc_info_less['cities']
        sch_loc_info['zones'] += sch_loc_info_less['zones']

In [12]:
sch_df = pd.concat([pd.DataFrame(sch_jsn), pd.DataFrame(sch_loc_info)], axis=1)

In [13]:
null_indices = sch_df[sch_df.isnull().any(axis=1)].index

In [14]:
for i in null_indices:

    ps = sch_df['Post Code'].iloc[i]

    PostcodeApi().get_pos_info(ps)

The postcode DD8 5BR is terminated.
The postcode DG3 5DS is terminated.
The postcode DG3 5DS is terminated.
The postcode DD5 3AE is terminated.
The postcode EH33 2LX is terminated.
Non-valid post code: EH7 4TN
The postcode KY8 1HL is terminated.
The postcode G20 8LY is terminated.
The postcode G33 3LT is terminated.
The postcode G33 3LT is terminated.
The postcode G21 1NL is terminated.
The postcode G33 4SA is terminated.
The postcode G2 4PF is terminated.
The postcode ML2 0LS is terminated.
The postcode ML2 0LS is terminated.
The postcode PH15 2DU is terminated.
The postcode PH15 2DU is terminated.
The postcode TD11 3QQ is terminated.
The postcode TD4 6HF is terminated.
The postcode KA7 1HX is terminated.
The postcode KA26 9AQ is terminated.
The postcode KA7 2PG is terminated.
The postcode ML9 1NJ is terminated.
The postcode G74 3QT is terminated.


In [15]:
sch_df.dropna(inplace=True)

In [22]:
sch_df['School Type'].unique()

array(['Primary', 'Secondary', 'Special'], dtype=object)

In [27]:
# Create a map centered at Edinburgh, the capital of Scotland
m = folium.Map(location=[55.941457, -3.205744], zoom_start=12)

# Create a custom color scale from light to dark blue
colors = {
    1: '#08306b',  # Dark blue (most deprived)
    2: '#08519c',
    3: '#3182bd',
    4: '#63b7f4',
    5: '#a6e1fa'   # Light blue (least deprived)
}

l = len(sch_df)

# Create circles and digits for each data point
for i in range(l):

    school = sch_df['School Name_x'].iloc[i]
    pos = sch_df['Post Code'].iloc[i]
    loc = sch_df['locs'].iloc[i]
    city = sch_df['cities'].iloc[i]
    zone = sch_df['zones'].iloc[i]
    pupils = sch_df['Total pupils'].iloc[i]
    type = sch_df['School Type'].iloc[i]

    try:
        mag = dep_rates[pos] # magnitute
    except:
        mag = 3 # average
    
    folium.CircleMarker(
        location=loc,
        radius=pupils/100,
        color=colors[mag],
        fill=True,
        fill_opacity=0.8,
    ).add_to(m)
    

    popup_html = f"""
    <h3>{school}</h3>
    <p><strong>Type:</strong> {type}</p>
    <p><strong>Local Authority:</strong> {city}</p>
    <p><strong>Zone:</strong> {zone}</p>
    <p><strong>Pupils:</strong> {pupils}</p>
    <p><strong>Deprivation:</strong> {mag}</p>"""

    folium.Marker(
        location=loc,
        popup=folium.Popup(popup_html, max_width=150),
        icon=folium.DivIcon(html=f'<div style="width: 0px; height: 0px;"></div>'),
    ).add_to(m)

# Create a custom HTML legend
legend_html = """
<div style="position: fixed; top: 10px; right: 10px; background-color: white; padding: 10px; border: 2px solid black; z-index: 1000;">
    <p><strong>Legend</strong></p>
    <p><span style="color: black;"><span style="background-color: #08306b; width: 20px; height: 20px; display: inline-block;"></span> 1 - Most Deprived</span></p>
    <p><span style="color: black;"><span style="background-color: #08519c; width: 20px; height: 20px; display: inline-block;"></span> 2</span></p>
    <p><span style="color: black;"><span style="background-color: #3182bd; width: 20px; height: 20px; display: inline-block;"></span> 3</span></p>
    <p><span style="color: black;"><span style="background-color: #63b7f4; width: 20px; height: 20px; display: inline-block;"></span> 4</span></p>
    <p><span style="color: black;"><span style="background-color: #a6e1fa; width: 20px; height: 20px; display: inline-block;"></span> 5 - Least Deprived</span></p>
</div>
"""
m.get_root().html.add_child(folium.Element(legend_html))

m.save('scottish_schools.html')

# Display the map (optional, this works in Jupyter Notebook)
m